In [ ]:
from google.colab import drive
drive.mount('/content/drive')

# Imports

In [ ]:
!pip install -q -U fastai fastcore pydub ffmpy
!pip install torchaudio librosa
!pip install fastai
!pip install fastcore==1.3.26
!pip install -q git+https://github.com/fastaudio/fastaudio.git --upgrade

In [ ]:
from fastai.vision import *
from fastai.vision.all import *
from fastai.data.all import *
import torchaudio
import IPython.display as ipd
import shutil
from pydub import AudioSegment
import os
from tqdm.notebook import trange
import ffmpy
from tqdm.notebook import trange

# Playback

In [ ]:
def play_back(file):
  waveform, sample_rate = torchaudio.load(file)
  return ipd.Audio(waveform, rate = sample_rate)

# Load 
Learner

In [ ]:
%cd /content/drive/MyDrive/Deploy_censor/
!ls

/content/drive/MyDrive/Deploy_censor
audio.m4a  censored	       censor_modelv3.pkl  output
audio.wav  censored_audio.wav  censor.wav	   output.wav


In [ ]:
m4a_file = 'audio.m4a'
wav_filename = "audio.wav"
from pydub import AudioSegment
track = AudioSegment.from_file(m4a_file,  format= 'm4a')
file_handle = track.export(wav_filename, format='wav')

In [ ]:
#  get censor audio file which will replace curse words and profanity in the audio file PREDICTION_FILE
CENSOR_FILE = 'censor.wav'
#  set prediction file path here
PREDICTION_FILE = 'audio.wav'
play_back(PREDICTION_FILE)

In [ ]:
# Returns class of a file 0 or 1
def set_class(file_location):
  if 'speech_commands' in str(file_location):
    return 0 # label =0 if contains no swear words
  else:
    return 1 # label =1 if contains swear words

# Extract file name from file_location
def set_file_name(file_location):
  if 'speech_commands' in str(file_location):
    name = str(Path(file_location).parent.name)
  else:
    name = str(Path(file_location).stem)
  return name

# Creates a directory of name "directory_name"
def create_directory(directory_name): 
  if Path(directory_name).exists(): shutil.rmtree(directory_name)
  os.mkdir(directory_name)

# create a new file name according to specified directory file is placed in
def recreate_name(file_location, new_location):
  file_name = set_file_name(file_location) + str(Path(file_location).suffix)
  final_name = Path(new_location)/file_name
  return final_name

# copy file to new directory
def move_to_new_location(file_location, new_location):
  shutil.copyfile(file_location, recreate_name(file_location, new_location))

# Create a dataframe for train and test data and set target = class 0 or 1 
def create_dataframe(folder_name, data):
  print("Creating", folder_name)
  df = pd.DataFrame({'file_name': [recreate_name(i, folder_name) for i in data],
                      'target': [set_class(i) for i in data]})
  parallel(move_to_new_location, data, dir = folder_name, n_workers = mp.cpu_count()) 
  return df

In [ ]:
# Creates a directory of name "directory_name"
def create_directory(directory_name): 
  if Path(directory_name).exists(): shutil.rmtree(directory_name)
  os.mkdir(directory_name)

#  function to get length of file in milliseconds
def file_length(file):
  audio = AudioSegment.from_wav(file)
  return int(audio.duration_seconds * 1000)

# function to help splitting of files in parallel
def split_helper(i, file, folder, split_size):
  start_time = i 
  end_time = i + split_size
  output = Path(f'{folder}/audio_{i}{Path(file).suffix}')
  audio = AudioSegment.from_wav(file)
  audio[start_time:end_time].export(output, format=f'{Path(file).suffix[1:]}')
  
# function that makes use of split helper to return split files of testing audio
def get_split_files(file, folder = 'output', split_size = 1000):
  print("splitting testing audio file into",split_size/1000,"second files")
  folder = Path(folder)
  if folder.exists(): 
    shutil.rmtree(folder)
  os.mkdir(folder)
  total_size = file_length(file)
  parallel(split_helper, range(0, total_size, split_size), file = file, folder = folder, split_size = split_size)
  split_files = glob.glob(f'{folder}/audio*{Path(file).suffix}')
  split_files = sorted(split_files, key = lambda x: int(str(Path(x).stem).split('_')[-1]))
  return split_files

split_size = 2000 # time in milliseconds
output_folder = 'output'
files = get_split_files(PREDICTION_FILE, output_folder , split_size)



# function that censors all bad_words
# return censored file which is the same length as original file
def censor_words(file):
  ms = file_length(file)
  output = recreate_name(file,'censored')
  ffmpy.FFmpeg(inputs={str(CENSOR_FILE):''},\
               outputs={str(output): "-y -ss 00:00:00 -to 00:00:00."+str(ms)+' -c copy'}).run() 
  return output

# function that joins all split files and censor files to get back censored audio from original audio
def get_audio_back(files, file_name ):
  print("recreating audio file with censored bad words")
  print("get_audio_back",file_name)
  n = len(files)
  t = ''.join(['['+str(i)+':0]' for i in range(n)])
  ffmpy.FFmpeg(inputs={str(files[n-1]): "-y "+ " ".join(['-i ' + str(i) for i in files[:n-1]])},\
               outputs={file_name: "-filter_complex '"+str(t)+"concat=n="+str(n)+\
               ":v=0:a=1[out]' -map '[out]'"}).run()
    
  return file_name

def censor(file, seconds = 0.2, folder = 'output'):
  create_directory('censored')
  ms = int(seconds * 1000)
  files = get_split_files(file, Path(folder), ms)
  print("FILES",files)
  for i in trange(len(files)):
    pred = learn.predict(files[i])[0]
    if (int(pred) == 1): 
      print(f'swear word identified')
      files[i] = censor_words(files[i])

  file_name = get_audio_back(files,'censored_' +Path(file).stem + Path(file).suffix)
  return file_name

splitting testing audio file into 2.0 second files


In [ ]:
learn = load_learner('censor_modelv3.pkl', cpu=True, pickle_module=pickle)
CENSORED_FILE = censor(PREDICTION_FILE, seconds = 0.2)

/usr/local/lib/python3.7/dist-packages/torchaudio/backend/utils.py:47: UserWarning: "torchaudio.USE_SOUNDFILE_LEGACY_INTERFACE" flag is deprecated and will be removed in 0.9.0. Please remove the use of flag.
  '"torchaudio.USE_SOUNDFILE_LEGACY_INTERFACE" flag is deprecated and will be removed in 0.9.0. '


splitting testing audio file into 0.2 second files
FILES ['output/audio_0.wav', 'output/audio_200.wav', 'output/audio_400.wav', 'output/audio_600.wav', 'output/audio_800.wav', 'output/audio_1000.wav', 'output/audio_1200.wav', 'output/audio_1400.wav', 'output/audio_1600.wav', 'output/audio_1800.wav', 'output/audio_2000.wav', 'output/audio_2200.wav', 'output/audio_2400.wav', 'output/audio_2600.wav', 'output/audio_2800.wav', 'output/audio_3000.wav', 'output/audio_3200.wav', 'output/audio_3400.wav', 'output/audio_3600.wav', 'output/audio_3800.wav', 'output/audio_4000.wav', 'output/audio_4200.wav', 'output/audio_4400.wav', 'output/audio_4600.wav', 'output/audio_4800.wav', 'output/audio_5000.wav', 'output/audio_5200.wav', 'output/audio_5400.wav', 'output/audio_5600.wav', 'output/audio_5800.wav', 'output/audio_6000.wav', 'output/audio_6200.wav', 'output/audio_6400.wav', 'output/audio_6600.wav']


  0%|          | 0/34 [00:00<?, ?it/s]

swear word identified


swear word identified


...

swear word identified


swear word identified


swear word identified


swear word identified


recreating audio file with censored bad words
get_audio_back censored_audio.wav


In [ ]:
play_back(PREDICTION_FILE)

In [ ]:
play_back(CENSORED_FILE)